In [8]:
import pandas as pd 
import ast
from ast import literal_eval
import numpy as np
from pandas import DataFrame

#setting the file we want to read
file = "train.csv"

#reading from CSV
df = pd.read_csv(file, header= 0, quotechar='"', sep=',', encoding = "ISO-8859-1",keep_default_na=True, 
                dtype = { 'belongs_to_collection' : 'category',  'genres' : 'category', 'original_language' : 'category', 'production_companies' : 'category', 'production_countries' : 'category',  'spoken_languages' : 'category', 'Keywords' : 'category', 'cast' : 'category', 'crew' : 'category'},
                na_values = [0]
                )

#setting the list to be edited
dataList = { 'belongs_to_collection',  'genres', 'production_companies', 'production_countries',  'spoken_languages', 'Keywords', 'cast', 'crew'}
dataID = { 'belongs_to_collection' : 'id',  'genres': 'id', 'production_companies': 'id', 'production_countries': 'iso_3166_1',  'spoken_languages': 'iso_639_1', 'Keywords': 'id', 'cast': 'id', 'crew': 'id'}
dataNeeded = ['id', 'belongs_to_collection', 'budget', 'genres', 'original_language',
       'popularity', 'production_companies', 'production_countries',
       'release_date', 'runtime', 'spoken_languages', 'Keywords',
       'cast', 'crew', 'revenue']

#dropping the columns that was not needed
for col in df.keys():
    if not (col in dataNeeded) :
        df = df.drop(columns = col)

#filling empty list with []
for col in dataList :
    try:
        df[col] = df[col].cat.add_categories('[]',inplace = False)
    except:
        pass
    df[col].fillna( '[]' , inplace = True) 

#changing a sting of list into list
for col in dataList :
    df[[col]] = df[[col]].applymap(literal_eval)     

#changing the dict in the list into ID only
for col in dataList : 
    for row in range(len(df)) :
        for num in range(len(df[col][row])) :
            if not (isinstance(df[col][row][num], int) or isinstance(df[col][row][num], str)):
                df[col][row][num] = df[col][row][num][dataID[col]]

uniqueSpokenLanguage = df['spoken_languages'].apply(pd.Series).stack().value_counts().keys().values.tolist()
for row in range(len(df)) :
    for num in range(len(df['spoken_languages'][row])):
        df['spoken_languages'][row][num] = uniqueSpokenLanguage.index(df.spoken_languages[row][num])

uniqueOrgLanguage = df['original_language'].unique().tolist()
df.original_language = df.original_language.replace(uniqueOrgLanguage,range(len(uniqueOrgLanguage)))

uniqueCountries = df['production_countries'].apply(pd.Series).stack().value_counts().keys().values.tolist()

for row in range(len(df)) :
    for num in range(len(df['production_countries'][row])):
        df['production_countries'][row][num] = uniqueCountries.index(df.production_countries[row][num])


df.head()

id belongs_to_collection      budget                  genres  \
0   1              [313576]  14000000.0                    [35]   
1   2              [107674]  40000000.0  [35, 18, 10751, 10749]   
2   3                    []   3300000.0                    [18]   
3   4                    []   1200000.0                [53, 18]   
4   5                    []         NaN                [28, 53]   

   original_language  popularity production_companies production_countries  \
0                  0    6.575393        [4, 60, 8411]                  [0]   
1                  0    8.248895                  [2]                  [0]   
2                  0   64.299990  [2266, 3172, 32157]                  [0]   
3                  1    3.174936                   []                  [5]   
4                  2    1.148070                   []                 [15]   

  release_date  runtime spoken_languages  \
0      2/20/15     93.0              [0]   
1     8/6/2004    113.0              [0]   
2   10/10/2014    105.0              [0]   
3     3/9/2012    122.0           [0, 8]   
4     2/5/2009    118.0             [11]   

                                            Keywords  \
0                        [4379, 9663, 11830, 179431]   
1                          [2505, 4263, 6038, 13072]   
2  [1416, 1523, 1640, 2176, 14512, 14819, 33896, ...   
3  [10092, 10540, 11734, 14536, 14636, 208364, 22...   
4                                                 []   

                                                cast  \
0  [52997, 64342, 54729, 36801, 54812, 94098, 115...   
1  [1813, 5823, 1210, 655, 33656, 62064, 68287, 1...   
2  [996701, 18999, 129104, 970216, 223012, 159366...   
3  [35068, 85047, 1021524, 1093644, 86033, 92686,...   
4                     [84751, 64453, 84752, 1130534]   

                                                crew   revenue  
0  [1449071, 3227, 347335, 347335, 57822, 1451395...  12314651  
1  [1201, 1214, 4500, 8851, 12970, 38415, 38416, ...  95149435  
2  [494, 6745, 9250, 23783, 23786, 53181, 52443, ...  13092000  
3                              [95510, 95510, 95510]  16000000  
4                                     [84749, 84749]   3923970

In [11]:
# getting all unique values
unique = {}

for col in dataList:
    print (col)
    abc = np.unique(df[col]).tolist()
    unique.update( {col: abc} )
    
#print(unique)
print(unique['belongs_to_collection'][0:5])
print(unique['production_countries'][0:5])
print()
#df.belongs_to_collection = df.belongs_to_collection.replace(unique["belongs_to_collection"],range(len(unique["belongs_to_collection"])),regex=True)

#for dataList, do one hot
for col in dataList: 
    #print (col)
    #print(df[col][0:5])
    for i, num in enumerate(df[col]):
        print("i",i)
        print("num", num)
        print("df[col][num]",df[col][i])
        #print(unique[col].index(df[col][num]))
        df[col][i] = unique[col].index(df[col][i])
    #df[col] = df[col].replace(unique[col],range(len(unique[col])),regex=False)

belongs_to_collection
production_countries
cast
genres
production_companies
spoken_languages
crew
Keywords
[[], [10], [84], [119], [151]]
[[], [0], [0, 1], [0, 1, 2, 7], [0, 1, 3]]

i 0
num [313576]
df[col][num] [313576]
i 1
num [107674]
df[col][num] [107674]
i 2
num []
df[col][num] []
i 3
num []
df[col][num] []
i 4
num []
df[col][num] []
i 5
num []
df[col][num] []
i 6
num []
df[col][num] []


C:\Users\isabe\Anaconda3\envs\env1\lib\site-packages\ipykernel_launcher.py:24: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy


i 7
num []
df[col][num] []
i 8
num [256377]
df[col][num] [256377]
i 9
num []
df[col][num] []
i 10
num [1575]
df[col][num] [1575]
i 11
num [48190]
df[col][num] [48190]
i 12
num []
df[col][num] []
i 13
num [91698]
df[col][num] [91698]
i 14
num []
df[col][num] []
i 15
num []
df[col][num] []
i 16
num []
df[col][num] []
i 17
num []
df[col][num] []
i 18
num []
df[col][num] []
i 19
num [9518]
df[col][num] [9518]
i 20
num []
df[col][num] []
i 21
num [9735]
df[col][num] [9735]
i 22
num [207621]
df[col][num] [207621]
i 23
num []
df[col][num] []
i 24
num []
df[col][num] []
i 25
num []
df[col][num] []
i 26
num []
df[col][num] []
i 27
num []
df[col][num] []
i 28
num []
df[col][num] []
i 29
num []
df[col][num] []
i 30
num []
df[col][num] []
i 31
num []
df[col][num] []
i 32
num []
df[col][num] []
i 33
num [207632]
df[col][num] [207632]
i 34
num [90863]
df[col][num] [90863]
i 35
num []
df[col][num] []
i 36
num []
df[col][num] []
i 37
num []
df[col][num] []
i 38
num []
df[col][num] []
i 39
num []
df[co

In [12]:
df.head()


id belongs_to_collection      budget genres  original_language  popularity  \
0   1                   357  14000000.0    532                  0    6.575393   
1   2                   207  40000000.0    558                  0    8.248895   
2   3                     0   3300000.0    193                  0   64.299990   
3   4                     0   1200000.0    637                  1    3.174936   
4   5                     0         NaN    483                  2    1.148070   

  production_companies production_countries release_date  runtime  \
0                   64                    1      2/20/15     93.0   
1                    5                    1     8/6/2004    113.0   
2                 1570                    1   10/10/2014    105.0   
3                    0                  131     3/9/2012    122.0   
4                    0                  212     2/5/2009    118.0   

  spoken_languages Keywords  cast  crew   revenue  
0                1     2156  2203  2958  12314651  
1                1     1896   540   622  95149435  
2                1     1563  2882   329  13092000  
3              105     2467  2025  2651  16000000  
4              296        0  2559  2604   3923970

In [13]:
# changing the time into numerical value

from datetime import datetime
from dateutil.parser import parse
import time
import datetime

x = datetime.datetime(1970, 1, 1)

for count in range(len(df)) :
    date = df.release_date[count]
    if (isinstance(date, str))and(date[-3] == "/"):
        if(int(date[-2], 10) < 2):
            df.release_date[count] = date[:-2] + '20' + date[-2:]
        else:
            df.release_date[count] = date[:-2] + '19' + date[-2:]
        #print(date)
        
    if (isinstance(date, str)):
        #print(date)
        df.release_date[count] = datetime.datetime.strptime(df.release_date[count], '%m/%d/%Y')

    if  isinstance(df.release_date[count], datetime.datetime):
        print(count, df.release_date[count])
        if(df.release_date[count].year >= 1970):
            df.release_date[count] =(df.release_date[count]-x).days + 365.25*15
        else:
            df.release_date[count] = (df.release_date[count].year-1955)*365.25 + (df.release_date[count].month-1)*(365.25/12)+(df.release_date[count].day-1)
        #print(df.release_date[count])

C:\Users\isabe\Anaconda3\envs\env1\lib\site-packages\ipykernel_launcher.py:14: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  
C:\Users\isabe\Anaconda3\envs\env1\lib\site-packages\ipykernel_launcher.py:21: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
C:\Users\isabe\Anaconda3\envs\env1\lib\site-packages\ipykernel_launcher.py:26: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy


0 2015-02-20 00:00:00
1 2004-08-06 00:00:00
2 2014-10-10 00:00:00
3 2012-03-09 00:00:00
4 2009-02-05 00:00:00
5 1987-08-06 00:00:00
6 2012-08-30 00:00:00
7 2004-01-15 00:00:00
8 1996-02-16 00:00:00
9 2003-04-16 00:00:00
10 1976-11-21 00:00:00
11 1987-07-10 00:00:00
12 1999-09-15 00:00:00
13 2005-03-04 00:00:00


C:\Users\isabe\Anaconda3\envs\env1\lib\site-packages\ipykernel_launcher.py:16: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  app.launch_new_instance()


14 2002-06-20 00:00:00
15 2010-10-06 00:00:00
16 2005-08-04 00:00:00
17 2013-12-25 00:00:00
18 2011-02-02 00:00:00
19 2005-08-02 00:00:00
20 1998-04-03 00:00:00
21 1982-08-13 00:00:00
22 2012-07-28 00:00:00
23 2011-09-02 00:00:00
24 2006-09-09 00:00:00
25 1992-10-23 00:00:00
26 1997-09-08 00:00:00
27 2013-09-07 00:00:00
28 1986-08-08 00:00:00
29 2002-04-07 00:00:00
30 2011-11-02 00:00:00
31 2005-05-02 00:00:00
32 2015-10-21 00:00:00
33 2014-10-02 00:00:00
34 2007-08-08 00:00:00
35 2012-04-16 00:00:00
36 2000-01-28 00:00:00
37 1995-03-10 00:00:00
38 2013-09-13 00:00:00
39 1965-04-07 00:00:00


C:\Users\isabe\Anaconda3\envs\env1\lib\site-packages\ipykernel_launcher.py:28: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy


40 2006-04-26 00:00:00
41 1967-06-22 00:00:00
42 2000-03-03 00:00:00
43 2014-09-05 00:00:00
44 2005-02-04 00:00:00
45 2009-10-09 00:00:00
46 2006-03-23 00:00:00
47 2015-12-25 00:00:00
48 2017-03-24 00:00:00
49 1994-11-17 00:00:00
50 2008-01-30 00:00:00
51 1965-07-01 00:00:00
52 1980-06-24 00:00:00
53 1988-01-15 00:00:00
54 2016-02-19 00:00:00
55 1993-07-02 00:00:00
56 2009-08-05 00:00:00
57 1997-06-20 00:00:00
58 2008-06-24 00:00:00
59 2002-03-08 00:00:00
60 2006-11-14 00:00:00
61 1956-05-30 00:00:00
62 1998-01-16 00:00:00
63 1989-07-28 00:00:00
64 2013-09-21 00:00:00
65 1988-02-26 00:00:00
66 2010-01-14 00:00:00
67 2013-10-04 00:00:00
68 1962-12-25 00:00:00
69 2006-06-03 00:00:00
70 2005-03-04 00:00:00
71 2004-02-06 00:00:00
72 1990-04-05 00:00:00
73 2004-03-30 00:00:00
74 1976-03-31 00:00:00
75 2011-08-18 00:00:00
76 2000-05-05 00:00:00
77 1980-07-25 00:00:00
78 1981-12-18 00:00:00
79 2016-09-15 00:00:00
80 2002-12-14 00:00:00
81 2005-10-21 00:00:00
82 2005-07-29 00:00:00
83 1984-12-

In [14]:
#check if all time is in float
for count in range(len(df)) :
    if  not isinstance(df.release_date[count], float):
        print (count,df.release_date[count])

In [15]:
df.head()

id belongs_to_collection      budget genres  original_language  popularity  \
0   1                   357  14000000.0    532                  0    6.575393   
1   2                   207  40000000.0    558                  0    8.248895   
2   3                     0   3300000.0    193                  0   64.299990   
3   4                     0   1200000.0    637                  1    3.174936   
4   5                     0         NaN    483                  2    1.148070   

  production_companies production_countries release_date  runtime  \
0                   64                    1      21964.8     93.0   
1                    5                    1      18114.8    113.0   
2                 1570                    1      21831.8    105.0   
3                    0                  131      20886.8    122.0   
4                    0                  212      19758.8    118.0   

  spoken_languages Keywords  cast  crew   revenue  
0                1     2156  2203  2958  12314651  
1                1     1896   540   622  95149435  
2                1     1563  2882   329  13092000  
3              105     2467  2025  2651  16000000  
4              296        0  2559  2604   3923970

In [16]:
# change the empty list back to nan
for x in dataList:
    df[x] = df[x].apply(lambda y: np.nan if y==0 else y)
df.head()

id  belongs_to_collection      budget  genres  original_language  \
0   1                  357.0  14000000.0   532.0                  0   
1   2                  207.0  40000000.0   558.0                  0   
2   3                    NaN   3300000.0   193.0                  0   
3   4                    NaN   1200000.0   637.0                  1   
4   5                    NaN         NaN   483.0                  2   

   popularity  production_companies  production_countries release_date  \
0    6.575393                  64.0                   1.0      21964.8   
1    8.248895                   5.0                   1.0      18114.8   
2   64.299990                1570.0                   1.0      21831.8   
3    3.174936                   NaN                 131.0      20886.8   
4    1.148070                   NaN                 212.0      19758.8   

   runtime  spoken_languages  Keywords    cast    crew   revenue  
0     93.0               1.0    2156.0  2203.0  2958.0  12314651  
1    113.0               1.0    1896.0   540.0   622.0  95149435  
2    105.0               1.0    1563.0  2882.0   329.0  13092000  
3    122.0             105.0    2467.0  2025.0  2651.0  16000000  
4    118.0             296.0       NaN  2559.0  2604.0   3923970

In [17]:
for col in dataList:
    print(unique[col][0:3])

[[], [10], [84]]
[[], [0], [0, 1]]
[[], [2, 8873, 35370, 97281, 142282, 1021393, 31117, 75315, 159067, 167381, 50708, 109996, 66304, 591, 160947, 1068, 102441], [3, 64, 515, 19957, 3905, 920, 77351, 84093, 925, 3982, 923, 140250, 65740, 155841, 157140, 1080064, 2368, 27037, 37205, 36218, 109667, 936505, 49275, 17200, 4492, 13310, 53249, 187683, 2550, 66994, 12797, 79025, 6580, 157986, 8175, 173756, 237370, 20563]]
[[], [12], [12, 14]]
[[], [1], [1, 4]]
[[], [0], [0, 1]]
[[], [1, 1, 1, 154, 1776, 4982, 9213, 9214, 9216, 9217, 9219, 9220], [1, 1, 1, 491, 488, 489, 492, 493, 508, 648, 664, 2689, 15017, 60536]]
[[], [30, 108, 237, 514, 566, 571, 726, 739, 744, 774, 776, 6054, 6271, 10093, 10508, 161207], [30, 222, 1700, 2038, 2051, 2303, 2304, 2305, 2307, 2309, 2461, 2462, 6009, 6262]]


In [18]:
df["original_language"][1460]

0

In [19]:
import math

for x in dataNeeded:
    for y in range(len(df)):
        #print(x)
        #print(df[x])
        print("                            ",x,y,df[x][y])
        if not (isinstance(df[x][y], float) or isinstance(df[x][y], int) or math.isnan(float(df[x][y]))):
            print(df[x][y],type(df[x][y]))
        
#x=float(df["belongs_to_collection"][3])  #abc

#print(math.isnan(x))

#math.isnan(df["belongs_to_collection"][3])

                             id 0 1
1 <class 'numpy.int64'>
                             id 1 2
2 <class 'numpy.int64'>
                             id 2 3
3 <class 'numpy.int64'>
                             id 3 4
4 <class 'numpy.int64'>
                             id 4 5
5 <class 'numpy.int64'>
                             id 5 6
6 <class 'numpy.int64'>
                             id 6 7
7 <class 'numpy.int64'>
                             id 7 8
8 <class 'numpy.int64'>
                             id 8 9
9 <class 'numpy.int64'>
                             id 9 10
10 <class 'numpy.int64'>
                             id 10 11
11 <class 'numpy.int64'>
                             id 11 12
12 <class 'numpy.int64'>
                             id 12 13
13 <class 'numpy.int64'>
                             id 13 14
14 <class 'numpy.int64'>
                             id 14 15
15 <class 'numpy.int64'>
                             id 15 16
16 <class 'numpy.int64'>
                    

In [34]:


df.to_csv('save.csv',index_label = False)

df_copy = pd.read_csv('save.csv')

In [35]:
df.head()

id  belongs_to_collection      budget  genres  original_language  \
0   1                  357.0  14000000.0   532.0                  0   
1   2                  207.0  40000000.0   558.0                  0   
2   3                    NaN   3300000.0   193.0                  0   
3   4                    NaN   1200000.0   637.0                  1   
4   5                    NaN         NaN   483.0                  2   

   popularity  production_companies  production_countries release_date  \
0    6.575393                  64.0                   1.0      21964.8   
1    8.248895                   5.0                   1.0      18114.8   
2   64.299990                1570.0                   1.0      21831.8   
3    3.174936                   NaN                 131.0      20886.8   
4    1.148070                   NaN                 212.0      19758.8   

   runtime  spoken_languages  Keywords    cast    crew   revenue  
0     93.0               1.0    2156.0  2203.0  2958.0  12314651  
1    113.0               1.0    1896.0   540.0   622.0  95149435  
2    105.0               1.0    1563.0  2882.0   329.0  13092000  
3    122.0             105.0    2467.0  2025.0  2651.0  16000000  
4    118.0             296.0       NaN  2559.0  2604.0   3923970

In [36]:
df_copy.head()

id  belongs_to_collection      budget  genres  original_language  \
0   1                  357.0  14000000.0   532.0                  0   
1   2                  207.0  40000000.0   558.0                  0   
2   3                    NaN   3300000.0   193.0                  0   
3   4                    NaN   1200000.0   637.0                  1   
4   5                    NaN         NaN   483.0                  2   

   popularity  production_companies  production_countries  release_date  \
0    6.575393                  64.0                   1.0      21964.75   
1    8.248895                   5.0                   1.0      18114.75   
2   64.299990                1570.0                   1.0      21831.75   
3    3.174936                   NaN                 131.0      20886.75   
4    1.148070                   NaN                 212.0      19758.75   

   runtime  spoken_languages  Keywords    cast    crew   revenue  
0     93.0               1.0    2156.0  2203.0  2958.0  12314651  
1    113.0               1.0    1896.0   540.0   622.0  95149435  
2    105.0               1.0    1563.0  2882.0   329.0  13092000  
3    122.0             105.0    2467.0  2025.0  2651.0  16000000  
4    118.0             296.0       NaN  2559.0  2604.0   3923970

In [39]:
import sklearn

print(sklearn.__version__)

from sklearn import impute
import sys
from impyute.imputation.cs import fast_knn

sys.setrecursionlimit(100000) #Increase the recursion limit of the OS

imputed_training=fast_knn(df.values, k=30)

0.20.3


BadInputError: Data is not float.

In [43]:
df_temp = df
df_temp.columns = range(df.shape[1])

df_temp.head()

0      1           2      3   4          5       6      7        8      9   \
0   1  357.0  14000000.0  532.0   0   6.575393    64.0    1.0  21964.8   93.0   
1   2  207.0  40000000.0  558.0   0   8.248895     5.0    1.0  18114.8  113.0   
2   3    NaN   3300000.0  193.0   0  64.299990  1570.0    1.0  21831.8  105.0   
3   4    NaN   1200000.0  637.0   1   3.174936     NaN  131.0  20886.8  122.0   
4   5    NaN         NaN  483.0   2   1.148070     NaN  212.0  19758.8  118.0   

      10      11      12      13        14  
0    1.0  2156.0  2203.0  2958.0  12314651  
1    1.0  1896.0   540.0   622.0  95149435  
2    1.0  1563.0  2882.0   329.0  13092000  
3  105.0  2467.0  2025.0  2651.0  16000000  
4  296.0     NaN  2559.0  2604.0   3923970

In [55]:
df.iloc[100]

0         101
1         NaN
2       7e+06
3         494
4           0
5      7.9585
6        1534
7           1
8     12808.8
9          91
10          1
11       1927
12       1623
13        588
14    9229401
Name: 100, dtype: object

In [57]:
from fancyimpute import KNN 
#We use the train dataframe from Titanic dataset
#fancy impute removes column names.
train_cols = list(df)

df_temp = pd.DataFrame(KNN(k=5).fit_transform(df_temp))

df_temp.columns = train_cols

C:\Users\isabe\Anaconda3\envs\env1\lib\site-packages\fancyimpute\solver.py:58: UserWarning: Input matrix is not missing any values
  warnings.warn("Input matrix is not missing any values")


Imputing row 1/3000 with 0 missing, elapsed time: 1.221
Imputing row 101/3000 with 0 missing, elapsed time: 1.221
Imputing row 201/3000 with 0 missing, elapsed time: 1.222
Imputing row 301/3000 with 0 missing, elapsed time: 1.222
Imputing row 401/3000 with 0 missing, elapsed time: 1.222
Imputing row 501/3000 with 0 missing, elapsed time: 1.222
Imputing row 601/3000 with 0 missing, elapsed time: 1.222
Imputing row 701/3000 with 0 missing, elapsed time: 1.222
Imputing row 801/3000 with 0 missing, elapsed time: 1.223
Imputing row 901/3000 with 0 missing, elapsed time: 1.223
Imputing row 1001/3000 with 0 missing, elapsed time: 1.223
Imputing row 1101/3000 with 0 missing, elapsed time: 1.223
Imputing row 1201/3000 with 0 missing, elapsed time: 1.223
Imputing row 1301/3000 with 0 missing, elapsed time: 1.223
Imputing row 1401/3000 with 0 missing, elapsed time: 1.224
Imputing row 1501/3000 with 0 missing, elapsed time: 1.224
Imputing row 1601/3000 with 0 missing, elapsed time: 1.224
Imputing 

In [59]:
df_temp.iloc[100]

0     1.010000e+02
1     2.178939e+02
2     7.000000e+06
3     4.940000e+02
4     0.000000e+00
5     7.958502e+00
6     1.534000e+03
7     1.000000e+00
8     1.280875e+04
9     9.100000e+01
10    1.000000e+00
11    1.927000e+03
12    1.623000e+03
13    5.880000e+02
14    9.229401e+06
Name: 100, dtype: float64

In [60]:
df_temp.head()

0           1             2      3    4          5            6      7   \
0  1.0  357.000000  1.400000e+07  532.0  0.0   6.575393    64.000000    1.0   
1  2.0  207.000000  4.000000e+07  558.0  0.0   8.248895     5.000000    1.0   
2  3.0  366.786451  3.300000e+06  193.0  0.0  64.299990  1570.000000    1.0   
3  4.0  237.963316  1.200000e+06  637.0  1.0   3.174936  1253.869350  131.0   
4  5.0  285.424741  4.034502e+06  483.0  2.0   1.148070  1563.170247  212.0   

         8      9      10           11      12      13          14  
0  21964.75   93.0    1.0  2156.000000  2203.0  2958.0  12314651.0  
1  18114.75  113.0    1.0  1896.000000   540.0   622.0  95149435.0  
2  21831.75  105.0    1.0  1563.000000  2882.0   329.0  13092000.0  
3  20886.75  122.0  105.0  2467.000000  2025.0  2651.0  16000000.0  
4  19758.75  118.0  296.0   594.265267  2559.0  2604.0   3923970.0

In [45]:
for col in dataNeeded:
    print(col, "\t\t\t",type(df[col].dtype))
    print("")

id 			 <class 'numpy.dtype'>

belongs_to_collection 			 <class 'numpy.dtype'>

budget 			 <class 'numpy.dtype'>

genres 			 <class 'numpy.dtype'>

original_language 			 <class 'numpy.dtype'>

popularity 			 <class 'numpy.dtype'>

production_companies 			 <class 'numpy.dtype'>

production_countries 			 <class 'numpy.dtype'>

release_date 			 <class 'numpy.dtype'>

runtime 			 <class 'numpy.dtype'>

spoken_languages 			 <class 'numpy.dtype'>

Keywords 			 <class 'numpy.dtype'>

cast 			 <class 'numpy.dtype'>

crew 			 <class 'numpy.dtype'>

revenue 			 <class 'numpy.dtype'>



In [44]:
df['id'].dtype

dtype('int64')